# Classification Example
##### Using Titanic dataset from kaggle.com

In [1]:
### Steps ###

# Problem Statement: Predict who will survive on the Titanic
# EDA
# Data cleaning
# Feature engineering
# Model training
# Model evaluation

In [2]:
# Load libraries

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt 

from sklearn.preprocessing import OneHotEncoder
from sklearn.tree import DecisionTreeClassifier
from sklearn import tree
from sklearn.model_selection import cross_val_score

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

%matplotlib inline

In [3]:
# Import data

df = pd.read_csv('C:/Users/scarl/Documents/Data/titanic.csv')
df.head()
df.info()
df.describe()
df.describe(include=['O'])

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S  
4      0            373450   8.0500   NaN        S

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 12 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  891 non-null    int64  
 1   Survived     891 non-null    int64  
 2   Pclass       891 non-null    int64  
 3   Name         891 non-null    object 
 4   Sex          891 non-null    object 
 5   Age          714 non-null    float64
 6   SibSp        891 non-null    int64  
 7   Parch        891 non-null    int64  
 8   Ticket       891 non-null    object 
 9   Fare         891 non-null    float64
 10  Cabin        204 non-null    object 
 11  Embarked     889 non-null    object 
dtypes: float64(2), int64(5), object(5)
memory usage: 83.7+ KB


PassengerId    Survived      Pclass         Age       SibSp  \
count   891.000000  891.000000  891.000000  714.000000  891.000000   
mean    446.000000    0.383838    2.308642   29.699118    0.523008   
std     257.353842    0.486592    0.836071   14.526497    1.102743   
min       1.000000    0.000000    1.000000    0.420000    0.000000   
25%     223.500000    0.000000    2.000000   20.125000    0.000000   
50%     446.000000    0.000000    3.000000   28.000000    0.000000   
75%     668.500000    1.000000    3.000000   38.000000    1.000000   
max     891.000000    1.000000    3.000000   80.000000    8.000000   

            Parch        Fare  
count  891.000000  891.000000  
mean     0.381594   32.204208  
std      0.806057   49.693429  
min      0.000000    0.000000  
25%      0.000000    7.910400  
50%      0.000000   14.454200  
75%      0.000000   31.000000  
max      6.000000  512.329200

Name   Sex    Ticket    Cabin Embarked
count                                 891   891       891      204      889
unique                                891     2       681      147        3
top     Beane, Mrs. Edward (Ethel Clarke)  male  CA. 2343  B96 B98        S
freq                                    1   577         7        4      644

In [5]:
# Data cleaning pass 1 - we already know there are missing values for Age (num), Cabin (cat), & Embarked (cat)

df[df['Age'].isna()].head()
df[df['Cabin'].isna()].head()
df[df['Embarked'].isna()].head()

PassengerId  Survived  Pclass                           Name     Sex  Age  \
5             6         0       3               Moran, Mr. James    male  NaN   
17           18         1       2   Williams, Mr. Charles Eugene    male  NaN   
19           20         1       3        Masselmani, Mrs. Fatima  female  NaN   
26           27         0       3        Emir, Mr. Farred Chehab    male  NaN   
28           29         1       3  O'Dwyer, Miss. Ellen "Nellie"  female  NaN   

    SibSp  Parch  Ticket     Fare Cabin Embarked  
5       0      0  330877   8.4583   NaN        Q  
17      0      0  244373  13.0000   NaN        S  
19      0      0    2649   7.2250   NaN        C  
26      0      0    2631   7.2250   NaN        C  
28      0      0  330959   7.8792   NaN        Q

PassengerId  Survived  Pclass                            Name     Sex  \
0            1         0       3         Braund, Mr. Owen Harris    male   
2            3         1       3          Heikkinen, Miss. Laina  female   
4            5         0       3        Allen, Mr. William Henry    male   
5            6         0       3                Moran, Mr. James    male   
7            8         0       3  Palsson, Master. Gosta Leonard    male   

    Age  SibSp  Parch            Ticket     Fare Cabin Embarked  
0  22.0      1      0         A/5 21171   7.2500   NaN        S  
2  26.0      0      0  STON/O2. 3101282   7.9250   NaN        S  
4  35.0      0      0            373450   8.0500   NaN        S  
5   NaN      0      0            330877   8.4583   NaN        Q  
7   2.0      3      1            349909  21.0750   NaN        S

PassengerId  Survived  Pclass                                       Name  \
61            62         1       1                        Icard, Miss. Amelie   
829          830         1       1  Stone, Mrs. George Nelson (Martha Evelyn)   

        Sex   Age  SibSp  Parch  Ticket  Fare Cabin Embarked  
61   female  38.0      0      0  113572  80.0   B28      NaN  
829  female  62.0      0      0  113572  80.0   B28      NaN

In [6]:
# Data cleaning - imputing missing values

df['Age'] = df['Age'].fillna(df['Age'].mean()) # Using the mean age
df['Embarked'] = df['Embarked'].fillna('S') # Using the mode embarked

In [7]:
df.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S  
4      0            373450   8.0500   NaN        S

In [8]:
# Feature engineering

features = ['Pclass', 'Sex', 'Age', 'SibSp', 'Parch', 'Fare', 'Embarked']
label = 'Survived'

df_features = df[features]
s_label = df[label]

In [9]:
# Preparation for modelling - encoding for categorical features

encoder = OneHotEncoder()
encoded_arr = encoder.fit_transform(df_features[['Sex', 'Embarked']]).toarray()
encoded_arr
encoder.categories_

array([[0., 1., 0., 0., 1.],
       [1., 0., 1., 0., 0.],
       [1., 0., 0., 0., 1.],
       ...,
       [1., 0., 0., 0., 1.],
       [0., 1., 1., 0., 0.],
       [0., 1., 0., 1., 0.]])

[array(['female', 'male'], dtype=object), array(['C', 'Q', 'S'], dtype=object)]

In [10]:
df_encoded = pd.DataFrame(encoded_arr, columns=['Sex=female', 'Sex=male', 'Embarked=C', 'Embarked=Q', 'Embarked=S']).astype(int)
df_encoded.head()

Sex=female  Sex=male  Embarked=C  Embarked=Q  Embarked=S
0           0         1           0           0           1
1           1         0           1           0           0
2           1         0           0           0           1
3           1         0           0           0           1
4           0         1           0           0           1

In [11]:
# Concatenate with original df

df_features = df_features.drop(columns=['Sex', 'Embarked'])
df_features = pd.concat([df_features, df_encoded], axis=1)
df_features.head()

Pclass   Age  SibSp  Parch     Fare  Sex=female  Sex=male  Embarked=C  \
0       3  22.0      1      0   7.2500           0         1           0   
1       1  38.0      1      0  71.2833           1         0           1   
2       3  26.0      0      0   7.9250           1         0           0   
3       1  35.0      1      0  53.1000           1         0           0   
4       3  35.0      0      0   8.0500           0         1           0   

   Embarked=Q  Embarked=S  
0           0           1  
1           0           0  
2           0           1  
3           0           1  
4           0           1

In [12]:
# Train DT model

model = DecisionTreeClassifier()
model.fit(df_features, s_label)

DecisionTreeClassifier(ccp_alpha=0.0, class_weight=None, criterion='gini',
                       max_depth=None, max_features=None, max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, presort='deprecated',
                       random_state=None, splitter='best')

In [13]:
fig, _ = plt.subplots(nrows=1, ncols=1, figsize=(100,50), dpi=300)
tree.plot_tree(
    model,
    feature_names=df_features.columns,
    filled=True)
fig.show()

[Text(11294.870833005352, 11067.613636363636, 'Sex=female <= 0.5\ngini = 0.473\nsamples = 891\nvalue = [549, 342]'),
 Text(3811.364776841939, 10552.84090909091, 'Age <= 6.5\ngini = 0.306\nsamples = 577\nvalue = [468, 109]'),
 Text(605.1637279596977, 10038.068181818182, 'SibSp <= 2.5\ngini = 0.444\nsamples = 24\nvalue = [8, 16]'),
 Text(448.99244332493697, 9523.295454545454, 'gini = 0.0\nsamples = 15\nvalue = [0, 15]'),
 Text(761.3350125944584, 9523.295454545454, 'Fare <= 31.331\ngini = 0.198\nsamples = 9\nvalue = [8, 1]'),
 Text(605.1637279596977, 9008.522727272728, 'gini = 0.0\nsamples = 5\nvalue = [5, 0]'),
 Text(917.5062972292191, 9008.522727272728, 'Fare <= 35.538\ngini = 0.375\nsamples = 4\nvalue = [3, 1]'),
 Text(761.3350125944584, 8493.75, 'gini = 0.0\nsamples = 1\nvalue = [0, 1]'),
 Text(1073.6775818639799, 8493.75, 'gini = 0.0\nsamples = 3\nvalue = [3, 0]'),
 Text(7017.565825724181, 10038.068181818182, 'Pclass <= 1.5\ngini = 0.28\nsamples = 553\nvalue = [460, 93]'),
 Text(2293

C:\Users\scarl\Anaconda3\3\lib\site-packages\ipykernel_launcher.py:6: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  


In [14]:
# Evaluate model - cross validation

accuracy_list = cross_val_score(model, df_features, s_label, cv=10)
print(f'The average accuracy is {(np.mean(accuracy_list)*100).round(2)}%')

The average accuracy is 77.22%
